# CPU vs. GPU Implementation for Solving Ku=f

In this notebook we investigate CPU runtime of 2 different methods for solve the following linear system

\begin{equation}
\mathbf{Ku}=\mathbf{f}
\end{equation}

The physical problem considered in this example is a steady-s

## Import Packages
Include ```ArrayFire.jl``` and ```EllipticFEM.jl``` packages as well as new types and functions needed to execute the above GPU implementation included in ```all_gpu_functions.jl```

In [3]:
#workspace()

# CUDArt.jl, CUSPARSE.jl and ArrayFire.jl packages
using CUDArt
using CUSPARSE
using ArrayFire

# standard EllipticFEM types and functions
include("./EllipticFEM/src/EllipticFEM.jl")

# additional GPU types and functions
include("./gpu_added_functions/all_gpu_functions.jl")

computeFunctionValuesAtElementsCentroids_GPU (generic function with 1 method)

## Import Equation Data and Build Geometry and Finite Element Matrices
Here we import the PDE equation parameters from the file ```ellipticEquationData.jl``` and generate geometric and mesh structures containing the necessary information to formulate a Finite Element Model (FEM)

In [4]:
# Assemble equation data from input file 'ellipticEquationData.jl'
println("Assemble equationData...")
equationData = equationDataAssemble("./ellipticEquationData.jl")

# Assemble geometric data (points, lines, etc.)
println("Assemble geoData...")
geoData = equationDataToGeoData(equationData)

# Generate unstructured mesh
intendedMeshsize = 0.5
println("Assemble meshData...")
meshData = geoDataToMeshData(geoData,intendedMeshsize)

# Assemble lseData
println("Assemble lseData...")
lseData = lseDataAssemble(equationData,meshData,0.0);

Assemble equationData...
Assemble geoData...
Assemble meshData...
Assemble lseData...


## Compare solver routines for single mesh
Here we compare the assembly routine ```lseDataSolve.jl``` found in the ```EllipticFEM.jl``` package with the newly created GPU Implementations of the Precondition Conjugate Gradient Method. We perform a single comparison over a mesh consisting of 13,385 nodes (13,385 DOFs).

In [17]:
# Preconditioned Conjugate Gradient Method

# define parameers
x0 = CudaArray(ones(length(lseData.r),))
maxIter = 200
tol = 0.01

# run solver
tic()
x = precondCG(lseData.M,CudaArray(lseData.r),x0,maxIter,tol)
elapsedTime = toq()

println("Time to solve Ku=f using PCG Method: $(elapsedTime) seconds")

Time to solve Ku=f using PCG Method: 0.57520886 seconds


In [28]:
h_x = to_host(x)

578-element Array{Float64,1}:
  0.999117
  1.0     
  0.999878
  0.998572
 21.7164  
 21.7164  
  1.15376 
  1.13517 
  1.12867 
  1.14387 
  1.12985 
  1.11839 
  1.14704 
  ⋮       
  1.43515 
  0.994537
  1.38163 
  1.26114 
  1.28898 
  1.32082 
  1.29299 
  1.41422 
  1.29131 
  1.33181 
  1.32047 
  1.27686 

In [20]:
# solve the system using EllipticFEM.jl package
println("Solve lseData...")
tic()
lseDataSolve(equationData,meshData,lseData)
elapsedTime2 = toq()

println("Time to solve Ku=f using EllipticFEM.jl solver: $(elapsedTime) seconds")

Solve lseData...
Time to solve Ku=f using EllipticFEM.jl solver: 0.57520886 seconds


In [27]:
lseData.solutions[1]

578-element Array{Float64,1}:
 35.0342
 37.1005
 38.5898
 32.3432
 25.0   
 25.0   
 38.9471
 39.3695
 39.4554
 39.0212
 36.2081
 36.6911
 36.2267
  ⋮     
 32.2737
 35.4871
 39.6724
 39.4596
 39.6599
 39.6996
 39.4964
 36.6273
 36.549 
 36.8054
 36.553 
 36.2275

## Compare solver routines for 10 different meshes of varying DOFs
Here we compare the solve routine ```lseDataSolve.jl``` found in the ```EllipticFEM.jl``` package with the newly created GPU Implementation of the Preconditioned Conjugate Gradient Method. We perform 10 comparisons over 10 different meshes consisting of sizes varying from 150 - 2.1M nodes (DOFs).  For each mesh size, we run 100 trials and average the runtimes

In [115]:
# Define array of mesh sizes (target size of element edge length)
#testMeshSizes = [1.0]
#testMeshSizes = [1.0,0.5]
testMeshSizes = [1.0,0.5,0.25,0.125,0.1,0.06125,0.03,0.01,0.0075]

# define arrays storing meshData and lseData
meshDataArray = Array{Any}(length(testMeshSizes),1)
nDOFsArray = zeros(length(testMeshSizes),1)
lseDataArray = Array{Any}(length(testMeshSizes),1)

for m = 1:length(testMeshSizes)
    meshDataArray[m] = geoDataToMeshData(geoData,testMeshSizes[m])
    nDOFsArray[m] = size(meshDataArray[m].nodes,2)
    lseDataArray[m] = lseDataAssemble(equationData,meshDataArray[m],0.0);
end

In [116]:
# number of trials for each run
nTrials = 100

# elapsedTime array for CPU runs
elapsedTimeTrials_CPU = zeros(nTrials+1,length(testMeshSizes))

# elapsedTime array for GPU runs
elapsedTimeTrials_GPU = zeros(nTrials+1,length(testMeshSizes));

### CPU Implementation Time Trials

In [127]:
gc()
for m in 1:length(testMeshSizes)
     
    for i in 1:nTrials+1
        
        # Solve Ku=f
        tic()
        lseDataSolve(equationData,meshDataArray[m],lseDataArray[m])
        elapsedTimeTrials_CPU[i,m] = toq()
        
    end
end

In [128]:
finalT_CPU = zeros(1,length(testMeshSizes))
finalT_CPU = sum(elapsedTimeTrials_CPU[2:end,:],1)./nTrials

1x9 Array{Float64,2}:
 0.000193007  0.00180929  0.00401581  …  0.16818  1.0071  13.153  25.5117

In [129]:
for kk = 1:length(testMeshSizes)
    println("Mesh Size: $(nDOFsArray[kk])")
    println("Average time to solve Ku=f : $(finalT_CPU[kk]) seconds")
    println("")
end

writedlm("CPU_solve_nDOFs.txt",nDOFsArray)
writedlm("CPU_solve_runtimes.txt",finalT_CPU)

Mesh Size: 150.0
Average time to solve Ku=f : 0.00019300732 seconds

Mesh Size: 578.0
Average time to solve Ku=f : 0.0018092908500000001 seconds

Mesh Size: 2181.0
Average time to solve Ku=f : 0.00401580903 seconds

Mesh Size: 8602.0
Average time to solve Ku=f : 0.03414059476 seconds

Mesh Size: 13385.0
Average time to solve Ku=f : 0.05421691168 seconds

Mesh Size: 36900.0
Average time to solve Ku=f : 0.16817990703 seconds

Mesh Size: 150679.0
Average time to solve Ku=f : 1.00709534864 seconds

Mesh Size: 1.325908e6
Average time to solve Ku=f : 13.153045341079999 seconds

Mesh Size: 2.364004e6
Average time to solve Ku=f : 25.511686587609997 seconds



### GPU Implementation Time Trials

In [111]:
# define parameers
x0 = CudaArray(zeros(length(lseData.r),))
maxIter = 100
tol = 0.01

0.01

In [112]:
gc()
for m in 1:length(testMeshSizes)
    
    for i in 1:nTrials+1
        
        # run solver
        tic()
        x = precondCG(lseData.M,CudaArray(lseData.r),x0,maxIter,tol)
        elapsedTimeTrials_GPU[i,m] = toq()
    
    end
end

In [113]:
finalT_GPU = zeros(length(testMeshSizes),1)
for k = 1:length(testMeshSizes)
    finalT_GPU[k] = sum(elapsedTimeTrials_GPU[2:end])./nTrials
end

In [114]:
for kk = 1:length(testMeshSizes)
    println("Mesh Size: $(nDOFsArray[kk])")
    println("Average time to solve Ku=f : $(finalT_GPU[kk]) seconds")
    println("")
end

writedlm("GPU_solve_nDOFs.txt",nDOFsArray)
writedlm("GPU_solve_runtimes.txt",finalT_GPU)

Mesh Size: 150.0
Average time to solve Ku=f : 0.8667741856899996 seconds

